In [1]:
import warnings
warnings.filterwarnings("ignore")

In [2]:
import pandas as pd
from pandas.tseries.offsets import MonthEnd
from pandas.tseries.offsets import Day
from pandas.tseries.offsets import BusinessDay as BDay
import numpy as np
import yfinance as yf
from datetime import datetime
from datetime import date
from datetime import timedelta
import concurrent.futures as cf

In [3]:
INIT_VAL = 100000
LOOKBACK_YEARS = 5

## Prep

In [4]:
monthly_constituents = pd.read_csv('./SP500_monthly_hist.csv')
monthly_constituents.set_index('Date', inplace=True)

In [5]:
ticker_list = set(monthly_constituents.to_numpy().flatten())
ticker_list.remove(np.nan)
ticker_list = [elem for elem in ticker_list if not elem[0].isnumeric()]

In [6]:
start_date_data = pd.to_datetime(monthly_constituents.index[0]) - pd.DateOffset(years=LOOKBACK_YEARS)
end_date_data = pd.to_datetime(monthly_constituents.index[-1]) + MonthEnd(0) + MonthEnd(1)

## Retrieving data from yahoo

In [7]:
type(True) == bool

True

In [8]:
# Retrieves relevant yahoo data for a single ticker
def retreive_yahoo_data_thread(ticker):
    stock = yf.Ticker(ticker)
    stock_hist = stock.history(start=start_date_data, end=end_date_data, interval='1d')
    if not stock_hist.index.empty:
        stock_hist.index = stock_hist.index.tz_localize(None)
        
        return {ticker: stock_hist['Close'].dropna()}
    else:
        return False

# Produces a dict with tickers and corresonding finance data to go with them.
def retreive_yahoo_data(tickers):
    
    tickers_data =  {}
    
    # Threading
    with cf.ThreadPoolExecutor() as executor:
        
        # Creates a thread for each ticker
        datarow = [executor.submit(retreive_yahoo_data_thread, ticker) for ticker in tickers]
        
        for row in cf.as_completed(datarow):
            # print('!!!!!!!!!!!!!!!!!!!!!!!!!')
            # print(row)
            # print(type(row))
            # print(row.result())
            # print(type(row.result()) == bool)
            try:
                if type(row.result()) != bool and not list(row.result().values())[0].empty:
                    # print('#####################')
                    # print(row.result())
                    # print(row.result()[0])
                    # print(row.result().Close[0])
                    tickers_data.update(row.result())
            except:
                pass
    return tickers_data

In [9]:
#Grabs market data for S&P500
market_index = yf.Ticker('^GSPC')
market_hist = market_index.history(start=start_date_data, end=end_date_data, interval='1d')
market_hist = market_hist[['Close']]
market_hist.index = market_hist.index.tz_localize(None)
daily_market_returns = market_hist.pct_change()

# all_ticker_data = retreive_yahoo_data(random.sample(ticker_list, 30))
all_ticker_data = retreive_yahoo_data(ticker_list)

- TWTR: No data found, symbol may be delisted
- CXO: No data found, symbol may be delisted
- XLNX: No data found, symbol may be delisted
- CERN: No data found, symbol may be delisted
- INFO: No data found, symbol may be delisted
- NLSN: No data found, symbol may be delisted
- DISCA: No data found, symbol may be delisted
- ETFC: No data found, symbol may be delisted
- DISCK: No data found, symbol may be delisted
- KSU: No data found, symbol may be delisted
- VAR: No data found, symbol may be delisted
- PBCT: No data found, symbol may be delisted
- HFC: No data found, symbol may be delisted
- CTXS: No data found, symbol may be delisted
- MXIM: No data found, symbol may be delisted
- ALXN: No data found, symbol may be delisted
- DRE: No data found, symbol may be delisted
- FLIR: No data found, symbol may be delisted
- NBL: No data found, symbol may be delisted
- MYL: No data found, symbol may be delisted


## Creating portfolio

In [10]:
def get_price_history_multi(tickers, start_date, end_date):
    combined_price_history = pd.DataFrame()
    for ticker in tickers:
        combined_price_history[ticker] = all_ticker_data[ticker].loc[start_date:end_date]
    combined_price_history.dropna()
    return combined_price_history

def get_price_history(ticker, start_date, end_date):
    price_history = pd.DataFrame()
    price_history['Close'] = all_ticker_data[ticker].loc[start_date:end_date]
    return price_history

def populate_next_month(all_ticker_data, portfolio, start_date, end_date):

    stocks = portfolio['Ticker']

    price_per_stock_df = pd.DataFrame()
    all_ticker_data_at_point = {x:all_ticker_data[x] for x in stocks if x in all_ticker_data}
    for ticker in all_ticker_data_at_point.keys():
        all_ticker_data_at_point[ticker] = all_ticker_data_at_point[ticker].loc[start_date:end_date]
        all_ticker_data_at_point[ticker].name = ticker
        price_per_stock_df = pd.concat([price_per_stock_df, all_ticker_data_at_point[ticker]], axis=1)
    
    shares_per_stock_df = price_per_stock_df.copy()
    i = 0
    for ticker in shares_per_stock_df.columns:
        shares_per_stock_df[ticker] = np.where(True, portfolio['Shares'].iloc[i], shares_per_stock_df[ticker])
        i += 1

    value_per_stock_df = shares_per_stock_df * price_per_stock_df

    value_per_stock_df['Total Value'] = value_per_stock_df.sum(axis=1)
    
    return value_per_stock_df[['Total Value']]

In [11]:
# Determines which ticker is the rickiest based on standard deviation and beta
def riskiest(tickers_data):
    largest3_std = tickers_data.nlargest(3, ['STD'])
    largest_beta = largest3_std.nlargest(1, ['Beta'])
    largest_beta.reset_index(inplace=True)
    return largest_beta

# produces a dataframe of the 10 stocks in the portfolio and their data
def other_9(tickers, correlator):

    correlation =  pd.DataFrame({'Ticker': [],
                                 'Price': [],
                                 'Beta': [],
                                 'STD': [],
                                 'Returns': [],
                                 'Corr': []})
    
    returns = pd.DataFrame(correlator['Returns'].iloc[0])
    returns.columns = ['Risky']
    
    for index in range(len(tickers.index)):
        if tickers['Ticker'].iloc[index] != correlator['Ticker'].iloc[0]:
            returns = returns[['Risky']]
            stock_returns = tickers['Returns'].iloc[index]
            returns = pd.concat([returns, stock_returns], join='inner', axis=1)
            correlation = pd.concat([correlation, pd.DataFrame({'Ticker': [tickers['Ticker'].iloc[index]],
                                                                'Price': [tickers['Price'].iloc[index]],
                                                                'Beta': [tickers['Beta'].iloc[index]],
                                                                'STD': [tickers['STD'].iloc[index]],
                                                                'Returns': [tickers['Returns'].iloc[index]],
                                                                'Corr': [returns.corr().iat[0,1]]})])
    
    most_correlated_20 = correlation.nlargest(20, 'Corr')
    risky_9 = most_correlated_20.nlargest(9, 'STD')
    final = pd.concat([correlator, risky_9])
    
    final.reset_index(inplace=True)
    final = final[['Ticker', 'Price', 'Beta', 'STD', 'Returns', 'Corr']]
    
    return final
       
 #Takes in a list of 10 tickers and produces weightings for a portfolio to maximise risk level
def weightings(tickers, availibleCash, start_date, end_date):

    #Creates list of tickers in the order of risk level 
    tickers10 = tickers['Ticker'].iloc[0:10].tolist()

    #Creates the initial weight distribution, which is not set in stone
    weights = [0.35, 0.05, 0.05, 0.05, 0.05, 0.05, 0.05, 0.05, 0.05, 0.05]

    #Creates a list to store tickers except the second to forth most risky stocks
    restTickers = tickers10[4:10]
    restTickers.insert(0, tickers10[0])

    #Creates a list for the weights for each of the stocks in RestTickers (these will not changed) 
    restweights = weights[4:10]
    restweights.insert(0, weights[0])

    #Gets data from yf for those tickers, and stores closing prices in a dataframe
    restprices = get_price_history_multi(restTickers, start_date, end_date)

    #Calculates the value of each of the 7 stocks based on each of their weights
    for ticker in restTickers:
        restprices[ticker+'_SharesPurchased'] = 0
        restprices[ticker+'_SharesPurchased'].iloc[0] = availibleCash * restweights[restTickers.index(ticker)] / restprices[ticker].iloc[-1]

    #Creates a column in the prices dataframe for the unchanging tickers with for the portfolio value overtime
    restprices['Portfolio_Value'] = 0
    restprices['Portfolio_Value'].iloc[0] = availibleCash * 0.65

    #Calculates the total portfolio value over time
    for x in range(1,len(restprices.index)):
        for ticker in restTickers:
            restprices['Portfolio_Value'].iloc[x] += restprices[ticker+'_SharesPurchased'].iloc[0] * restprices[ticker].iloc[x]

    #Creates a list of the tickers of the second, third and forth most risky stocks
    Two_Three_Four_Tickers = [tickers10[1], tickers10[2], tickers10[3]]

    #Gets closing prices from yahoo finance for each of these stocks
    prices = get_price_history_multi(Two_Three_Four_Tickers, start_date, end_date)

    #Sets the starting value of each stock to be $100000
    #We will later find a portion of the values when determining the riskest weightings for these stocks
    for ticker in Two_Three_Four_Tickers:
        prices[ticker+'_SharesPurchased']= 0
        prices[ticker+'_Value']=0
        prices[ticker+'_Value'].iloc[0]=availibleCash
        prices[ticker+'_SharesPurchased'].iloc[0] =  availibleCash / prices[ticker].iloc[0]
        
    #Calculates value over time for each stock
    for x in range(1,len(prices.index)):
        for ticker in Two_Three_Four_Tickers:
            prices[ticker+'_Value'].iloc[x] = prices[ticker+'_SharesPurchased'].iloc[0] * prices[ticker].iloc[x]

    #Combines the two dataframes into one that will contain all value and pricing data overtime
    combined = pd.concat([restprices,prices],join='inner', axis=1)

    #Creates a new dataframe to store standard deviations and their weightings
    totalstd = pd.DataFrame(index=range(0, 21))
    totalstd['Standard_Deviation'] = 0
    totalstd['Weight_3'] = 0

    #Creates a dataframe to store the value of each of the stocks that have a dynamic weightings
    value_2 = combined[tickers10[1]+"_Value"]
    value_3 = combined[tickers10[2]+"_Value"]
    value_4 = combined[tickers10[3]+"_Value"]

    #Loops through all possible ways to ditribute $20000 in portions of $1000
    for x in totalstd.index:
        
        #creates a dataframe to store the weightings of the first stock and the standard deviation that goes with it
        weight34 = pd.DataFrame(index=range(0,21-x))
        weight34['Standard_Deviation'] = 0

        #loops through all ways to distribute the remaining cash not used by the first stock to the second and third stock
        for y in range(0,21-x):
            #Calculates the value and standard deviation of the portfolio for the current weightings
            total_values = restprices.Portfolio_Value + (value_2 * (5+x)/100) + (value_3 * (5+y)/100) + (value_4 * (25-x-y)/100)
            portfolio = pd.DataFrame(total_values)
            returns = pd.DataFrame(portfolio.pct_change())

            #Adds the standard deviation to a dataframe
            weight34['Standard_Deviation'].iloc[y] = returns.std()[0]

        #Calculates the biggest standard devaition of the dataframe
        #  which changes how cash was distributed betweeen the second and third stock
        std1 = weight34['Standard_Deviation'].max()

        # print(tickers10[1])
        # print(tickers10[2])
        # print(tickers10[3])
        # print(value_2)
        # print(value_3)
        # print(value_4)
        # print(restprices.Portfolio_Value)
        # print(str(x) + ', ' + str(y))
        # print(total_values)
        # print(portfolio)
        # print(returns)
        # print(weight34)
        
        #Adds the max standard deviation and it's weights to another dataframe which 
        #  holds standard deviations for different amounts cash in the first stock
        weight3 = weight34.index[weight34['Standard_Deviation']==std1].tolist()[0]
        totalstd['Weight_3'].iloc[x] = weight3
        totalstd['Standard_Deviation'].iloc[x] = std1

    ## Determines the weighting for the stock with the biggest standard deviation
    weight2 = totalstd[totalstd.Standard_Deviation == totalstd['Standard_Deviation'].max()].index[0]
    weight3 = totalstd.loc[weight2, 'Weight_3']
    
    #Updates the weights in the original weights dataframe
    weights[1]=(5 + weight2)/100
    weights[2]=(5 + weight3)/100
    weights[3]=(25 - weight2 - weight3)/100  
    
    #Creates a final dataframe to output
    FinalPortfolio = tickers
    
    #adds weights to the dataframe
    FinalPortfolio['weights'] = pd.Series(weights)

    # Fixes the Price Column
    FinalPortfolio['Price'] = FinalPortfolio['Price'].apply(lambda x: x.Close)
    
    #Calculates number of shares of bought of each stock
    FinalPortfolio['Shares'] = (FinalPortfolio.weights * availibleCash) / FinalPortfolio.Price
    
    #Creates column for the value of each stock within the portfolio
    FinalPortfolio['Value'] = FinalPortfolio.weights * availibleCash
    
    #Creates a new colummn for the weights at the end of the dataframe with the numbers in terms of %
    FinalPortfolio['Weight'] = FinalPortfolio.weights * 100
    
    #Formatting
    FinalPortfolio = FinalPortfolio[['Ticker', 'Price', 'Shares', 'Value', 'Weight']]
    FinalPortfolio.columns = ['Ticker', 'Price', 'Shares', 'Value', 'Weight']
    
    #returns a final portfolio with the purchasing data for the stock being baught
    return(FinalPortfolio)

def produce_portfolio(all_ticker_data, start_date, end_date, eom_date, stocks, funds):

    # Gets data for current SP500 constituents and ensures there is data till the EOM
    all_ticker_data_at_point = {x:all_ticker_data[x] for x in stocks if x in all_ticker_data 
                                                                        and pd.DataFrame(all_ticker_data[x]).index[-1] >= eom_date
                                                                        and pd.DataFrame(all_ticker_data[x]).index[0] < end_date
    }
    
    # sets data to be within the past few years
    for ticker in list(all_ticker_data_at_point.keys()).copy():
        all_ticker_data_at_point[ticker] = all_ticker_data_at_point[ticker].loc[start_date:end_date]


    daily_market_returns_at_point = daily_market_returns.loc[start_date:end_date]

    input_data = pd.DataFrame({'Ticker': [],
                               'Price': [],
                               'Beta': [],
                               'STD': [],
                               'Returns': []})
    for ticker in all_ticker_data_at_point:

        prices = pd.DataFrame(all_ticker_data_at_point[ticker])
        returns = prices.pct_change()

        ####### Price #############
        price = prices.iloc[-1]

        ######## Beta #############
        returns['Market'] = daily_market_returns_at_point['Close']
        beta = (returns.cov() / daily_market_returns['Close'].var()).iat[1,0]

        ######### STD #############
        std = prices.pct_change().std()

        input_data = pd.concat([input_data, pd.DataFrame({'Ticker': [ticker], 'Price': [price], 'Beta': [beta], 'STD': [std.Close], 'Returns': [prices['Close'].pct_change()]})], ignore_index=True)

    risky1 = riskiest(input_data)

    final10 = other_9(input_data, risky1)

    FinalPortfolio = weightings(final10, funds, start_date, end_date)

    return FinalPortfolio

In [12]:
portfolio_history = pd.DataFrame()

current_value = INIT_VAL

i=1
for month in monthly_constituents.index:
    print(i, end='\r')
    i+=1
    
    end_date = pd.to_datetime(month)
    start_date = pd.to_datetime(month) - pd.DateOffset(years=LOOKBACK_YEARS)
    start_date = date(end_date.year - LOOKBACK_YEARS, end_date.month, end_date.day)
    eom_date = end_date + MonthEnd(0) + BDay(1)
    portfolio = produce_portfolio(all_ticker_data, start_date, end_date, eom_date, monthly_constituents.loc[month,:].to_numpy(), current_value)

    value_for_month_df = populate_next_month(all_ticker_data, portfolio, end_date, eom_date)

    current_value = value_for_month_df['Total Value'].iloc[-1]

    value_for_month_df = value_for_month_df.iloc[:-1,:]
    portfolio_history = pd.concat([portfolio_history, value_for_month_df])
try:
    shares_of_market = INIT_VAL / market_hist.loc[pd.Timestamp(monthly_constituents.index[0]) + BDay(0), 'Close']
except:
    shares_of_market = INIT_VAL / market_hist.loc[pd.Timestamp(monthly_constituents.index[0]) + BDay(2), 'Close']
market_hist['SP500'] = market_hist['Close'] * shares_of_market
portfolio_history = pd.concat([portfolio_history, market_hist['SP500']], join='inner', axis=1)

!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!
{'WEC': Date
2015-10-01    40.514996
2015-10-02    40.935081
2015-10-05    41.036209
2015-10-06    40.553886
2015-10-07    40.188259
                ...    
2020-09-25    87.883049
2020-09-28    88.038155
2020-09-29    88.202423
2020-09-30    88.421432
2020-10-01    89.653305
Name: Close, Length: 1260, dtype: float64, 'NWS': Date
2015-10-01    11.584645
2015-10-02    11.827679
2015-10-05    12.133719
2015-10-06    12.196731
2015-10-07    12.322746
                ...    
2020-09-25    13.576851
2020-09-28    13.858288
2020-09-29    13.363349
2020-09-30    13.567145
2020-10-01    13.732126
Name: Close, Length: 1260, dtype: float64, 'XOM': Date
2015-10-01    51.257046
2015-10-02    52.516666
2015-10-05    53.160324
2015-10-06    53.907799
2015-10-07    54.814445
                ...    
2020-09-25    29.907867
2020-09-28    30.486338
2020-09-29    29.597046
2020-09-30    29.640215
2020-10-01    28.604147
Name: Close, Length: 1260, dtype: float64, 'HPQ'

In [20]:
portfolio_history

Total Value          SP500
2020-10-01  100000.000000  100000.000000
2020-10-02  103592.303050   99042.234782
2020-10-05  106477.671413  100822.292015
2020-10-06  102405.643573   99413.450135
2020-10-07  104160.950005  101142.921558
...                   ...            ...
2023-09-25   93177.294049  128296.257654
2023-09-26   90930.978932  126405.872085
2023-09-27   91631.191152  126434.858728
2023-09-28   92684.648721  127179.961347
2023-09-29   92630.572614  126835.356802

[752 rows x 2 columns]

## Exporting

In [21]:
portfolio_history.index = portfolio_history.index.strftime("%m/%d/%y")
portfolio_history.T.to_json('portfolio_vs_sp500_hist.json')